In [ ]:
from pathlib import Path
import subprocess

# 是否使用 FRP 客户端
use_frpc = True
frpconfigfile = '/kaggle/input/aihua-5000/frpc_10669839.ini'

# 配置基础信息
server_addr = "frps.loliy.top"
server_port = 7500
token = "frps162534"
base_local_port = 7860  # 本地端口起始
base_remote_port = 10004  # 远程端口起始
num_services = 2  # 服务数量

# 生成配置内容
config = f"""
[common]
server_addr = {server_addr}
server_port = {server_port}
token = {token}
"""

# 生成服务配置
for i in range(num_services):
    remote_port = base_remote_port + i  # 远程端口
    service_name = f"sdwebuip{remote_port}"  # 使用远程端口作为服务名称
    local_port = base_local_port + i  # 本地端口
    config += f"""
[{service_name}]
type = tcp
local_ip = 127.0.0.1
local_port = {local_port}
remote_port = {remote_port}
"""

# 特殊的 SSH 服务配置
remote_port = base_remote_port + num_services  # SSH 的远程端口
config += f"""
[sdwebuip{remote_port}]
type = tcp
local_ip = 127.0.0.1
local_port = 22
remote_port = {remote_port}
"""

# 定义保存路径
file_path = './cyanfrp.ini'

# 将配置内容写入文件
with open(file_path, 'w') as config_file:
    config_file.write(config)

print(f"配置文件已创建为 {file_path}")

import os
import shutil
from pathlib import Path
import subprocess

# 启动 FRP 客户端函数
def install_Frpc(port, frpconfigfile, use_frpc):
    if use_frpc:
        frpc_path = '/kaggle/input/net-tools-new/frpc'  # 修改路径为新目录
        destination_path = '/kaggle/working/frpc'

        # 检查文件是否存在
        try:
            if not Path(frpc_path).exists():
                print(f"错误：FRP 客户端文件缺失！请确保文件存在于 {frpc_path}")
                return  # 文件不存在时退出函数，跳过后续操作
            else:
                print(f"文件 {frpc_path} 存在，准备复制到 {destination_path}")
        except Exception as e:
            print(f"检查文件存在时出错：{e}")

        # 如果目标路径已经有同名文件或目录，先删除
        try:
            if Path(destination_path).exists():
                print(f"目标路径 {destination_path} 已存在，正在删除旧文件或目录...")
                if Path(destination_path).is_dir():
                    shutil.rmtree(destination_path)  # 删除目录及其中的文件
                else:
                    os.remove(destination_path)  # 删除文件
        except Exception as e:
            print(f"删除目标路径时出错：{e}")

        # 确保目标目录存在
        try:
            target_dir = Path('/kaggle/working')
            if not target_dir.exists():
                print(f"目标目录不存在，创建中：{target_dir}")
                target_dir.mkdir(parents=True, exist_ok=True)
        except Exception as e:
            print(f"创建目标目录时出错：{e}")

        # 执行文件复制和权限更改
        try:
            subprocess.run(['cp', frpc_path, destination_path], check=True)
        except subprocess.CalledProcessError as e:
            print(f"复制文件时出错：{e}")
        except Exception as e:
            print(f"未知错误（复制文件）：{e}")

        # 执行文件权限更改
        try:
            subprocess.run(['chmod', '+x', destination_path], check=True)
        except subprocess.CalledProcessError as e:
            print(f"修改文件权限时出错：{e}")
        except Exception as e:
            print(f"未知错误（修改文件权限）：{e}")

        # 启动 FRP 客户端
        try:
            print(f'正在启动 FRP ，端口 {port}')
            subprocess.Popen([destination_path, '-c', str(Path(file_path).resolve())])
        except Exception as e:
            print(f"启动 FRP 客户端时出错：{e}")

# 启动 FRP
install_Frpc('5140', frpconfigfile, use_frpc)


----

# > <span style="color:green; font-weight:;"> Webui基础配置(可改也可不改) </span>

In [ ]:
# True 表示是 ， False 表示否
# 安装目录
install_path="/kaggle/working" #或者/kaggle
updata_webui = False  #是否开机自动更新webui

# 重置变量 会删掉sd_webui重新安装
reLoad = True
updata_webui = False

#清理和打包生成的图片
zip_output=True
clear_output=True
#打包环境减少下次启动时
use_zip_venv = False


# 使用huggingface保存和载入webui配置文件
huggingface_use = True
huggingface_token_file = '/kaggle/input/tenkens/hugfacetoken.txt'
huggiingface_repo_id = 'ACCA225/lovedraw'

# 环境包选择：
environment = 3
"""
环境包 1 ：pytorch 2.0.1+cu118 xformers 0.0.22 （已经炸了）
环境包 2 ：pytorch 2.1.1+cu121 xformers 0.0.23 （已经炸了）
环境包 3 ：pytorch 2.2.0+cu121 xformers 0.0.24
"""
python_version_attempt_fix = False #修复因为python版本不一致导致的no python file问题

------

# > <span style="color:green; font-weight:;">插件，模型地址 （添加模型在此代码单元格修改）</span>‘
## <span style="color:red; font-weight:bold;">上传模型方法见顶部的教程</span>
## <span style="color:red; font-weight:bold;">如果模型无法用下载链接载入，可选用上传到kaggle数据集方法来载入模型(见方法二)</span>
## 现在可以使用自定义模型文件名了！格式：['a.safetensors:b'] 其中a.safetensor为文件名，b为下载链接，用冒号隔开

In [ ]:
#模型和插件，下载的东西越多，启动速度更慢
# 更新代码时直接把这个粘贴到新代码就行
是否启用ControlNet = True #  开启后需要多花费2-3分钟来下载基本模型，你想快速启动可以关闭
是否启用SadTalker = False # 虚拟数字人插件，下载特定模型要花费1分钟时间，生成的视频保存在sd目录下的/results文件夹里
# 其它插件列表： git仓库地址
# 不需要的插件在前面加 # ，插件地址之间需要用英语逗号隔开
extensions = [
    'https://github.com/Elldreth/loopback_scaler',
    'https://github.com/jexom/sd-webui-depth-lib',
    'https://github.com/AlUlkesh/stable-diffusion-webui-images-browser', #图库浏览器
    #'https://github.com/camenduru/sd-civitai-browser', #C站助手
    #'https://github.com/Mikubill/sd-webui-controlnet', #控制网插件，神器！！
    'https://github.com/nonnonstop/sd-webui-3d-open-pose-editor', # 3D openpose，可以让你的老婆摆出你想要的姿势
    'https://openi.pcl.ac.cn/2575044704/stable-diffusion-webui-localization-zh_CN', #汉化
    'https://github.com/opparco/stable-diffusion-webui-two-shot', #潜变量成对
    #'https://github.com/minicacas/stable-diffusion-webui-composable-lora',
    'https://github.com/DominikDoom/a1111-sd-webui-tagcomplete', #tag自动补全
    'https://github.com/pkuliyi2015/multidiffusion-upscaler-for-automatic1111', #分块vae
    #'https://github.com/KohakuBlueleaf/a1111-sd-webui-locon',
    'https://github.com/hnmr293/sd-webui-cutoff', #Cutoff
    'https://github.com/hako-mikan/sd-webui-lora-block-weight', #Lora分层
    #'https://github.com/butaixianran/Stable-Diffusion-Webui-Civitai-Helper', #C站助手，请勿使用。有风险
    'https://github.com/catppuccin/stable-diffusion-webui', #UI修改，推荐
    #'https://github.com/Nevysha/Cozy-Nest',
    #'https://github.com/Scholar01/sd-webui-mov2mov', #AI视频转视频
    #'https://github.com/toriato/stable-diffusion-webui-wd14-tagger', #WD14打标器
    #'https://github.com/KohakuBlueleaf/a1111-sd-webui-lycoris', #LyCORIS插件，Lora升级版
    'https://github.com/deforum-art/sd-webui-deforum', #Deform，AI视频
    'https://github.com/zanllp/sd-webui-infinite-image-browsing', #云端用不了
    'https://github.com/KaggleSD/sd-extension-system-info',  #系统信息
    #'	https://github.com/d8ahazard/sd_dreambooth_extension', #Dreambooth训练
    #'https://github.com/viyiviyi/prompts-filter'
    'https://github.com/continue-revolution/sd-webui-animatediff',
    'https://github.com/adieyal/dynamicprompts',
    #'https://github.com/viyiviyi/sd-encrypt-image.git',
    'https://github.com/adieyal/sd-dynamic-prompts.git',
    'https://github.com/hako-mikan/sd-webui-supermerger',
    'https://github.com/Bing-su/adetailer',
    '',
    'https://github.com/Echoflare/a1111-sd-encrypt-image',
    "https://github.com/etherealxx/batchlinks-webui",
]


# Stable Diffusion模型数据集请放在这里（只填模型的目录即可）
sd_model = [
'/kaggle/input/9527-fp16',
"/kaggle/input/model-checkpoint/二次元收集",
"/kaggle/input/checkpoint*",
"/kaggle/input/noobnew"
            ]
# Stable Diffusion模型（Checkpoint）下载链接放这里
sd_model_urls=[
# majic Realistic
'[C站热门|真人]麦橘v6.safetensors:https://civitai.com/api/download/models/94640',
# null style v2
#'https://huggingface.co/swl-models/NullStyle-v2.0/resolve/main/NullStyle-v2.0.safetensors',
#'[二次元可爱画风]Cuteyukimix_mid3.safetensors:https://civitai.com/api/download/models/163923',
'[萌二次元]131-half.safetensors:https://huggingface.co/datasets/ACCC1380/private-model/resolve/main/kaggle/input/museum/131-half.safetensors',
# https://www.liblib.ai/modelinfo/331fb29f1f054f8cbdfaa88545b15a26 KlkilMix出处
'NoobXL-Epslion.safetensors:https://huggingface.co/datasets/ACCC1380/private-model/resolve/main/model/NoobXL-Epsilon-pred%200.5-Version.safetensors'
]

# VAE模型请放在这里（不用填模型的文件名，只填模型的目录即可）
vae_model = []
#VAE模型下载链接放这里
# 注意SDXL类模型的VAE不能与SD1.5的VAE混用，这是常识！
vae_model_urls=[
'131vae.vae.pt:https://huggingface.co/datasets/VASVASVAS/vae/resolve/main/pastel-waifu-diffusion.vae.pt',
]

# Lora模型的数据集路径请写在这里：
lora_model = [
#'/kaggle/input/lora-1',
"/kaggle/input/lora*"
]
# Lora模型下载链接放这里
lora_model_urls=[
#墨心
#'https://civitai.com/api/download/models/14856',
#山楂糕
#'https://civitai.com/api/download/models/41580',
#细节调整
'https://huggingface.co/amaru96vn/Add_Detail_Lora/resolve/main/add_detail.safetensors',
# LCM模型专用
'https://huggingface.co/latent-consistency/lcm-lora-sdv1-5/resolve/main/pytorch_lora_weights.safetensors',
#'https://huggingface.co/latent-consistency/lcm-lora-ssd-1b/resolve/main/pytorch_lora_weights.safetensors',
]
# Lycoris和loha模型的数据集路径请写在这里：
lyco_model = [
#'/kaggle/input/lora-1',
]
# Lycoris和loha模型下载链接放这里
lyco_model_urls=[
#FilmGirl 胶片风
#'https://civitai.com/api/download/models/75069',
#Teacher clothes 教师衣服
#"https://civitai.com/api/download/models/65426",
#伪日光
#'https://civitai.com/api/download/models/71235',
]

# ControlNet模型data请放在这里：
cn_model = [
]
# controlnet模型下载链接放这里
cn_model_urls = [
'https://huggingface.co/comfyanonymous/ControlNet-v1-1_fp16_safetensors/resolve/main/control_v11e_sd15_ip2p_fp16.safetensors',
'https://huggingface.co/comfyanonymous/ControlNet-v1-1_fp16_safetensors/resolve/main/control_v11e_sd15_shuffle_fp16.safetensors',
'https://huggingface.co/comfyanonymous/ControlNet-v1-1_fp16_safetensors/resolve/main/control_v11f1p_sd15_depth_fp16.safetensors',
'https://huggingface.co/comfyanonymous/ControlNet-v1-1_fp16_safetensors/resolve/main/control_v11p_sd15_canny_fp16.safetensors', #硬边缘检测
'https://huggingface.co/comfyanonymous/ControlNet-v1-1_fp16_safetensors/resolve/main/control_v11p_sd15_inpaint_fp16.safetensors',
'https://huggingface.co/comfyanonymous/ControlNet-v1-1_fp16_safetensors/resolve/main/control_v11p_sd15_lineart_fp16.safetensors',
'https://huggingface.co/comfyanonymous/ControlNet-v1-1_fp16_safetensors/resolve/main/control_v11p_sd15_mlsd_fp16.safetensors',
'https://huggingface.co/comfyanonymous/ControlNet-v1-1_fp16_safetensors/resolve/main/control_v11p_sd15_normalbae_fp16.safetensors',
'https://huggingface.co/comfyanonymous/ControlNet-v1-1_fp16_safetensors/resolve/main/control_v11p_sd15_openpose_fp16.safetensors', #姿态检测
'https://huggingface.co/comfyanonymous/ControlNet-v1-1_fp16_safetensors/resolve/main/control_v11p_sd15_scribble_fp16.safetensors',
'https://huggingface.co/comfyanonymous/ControlNet-v1-1_fp16_safetensors/resolve/main/control_v11p_sd15_softedge_fp16.safetensors',
'https://huggingface.co/comfyanonymous/ControlNet-v1-1_fp16_safetensors/resolve/main/control_v11p_sd15s2_lineart_anime_fp16.safetensors', #线稿
'https://huggingface.co/comfyanonymous/ControlNet-v1-1_fp16_safetensors/resolve/main/control_v11u_sd15_tile_fp16.safetensors', #分块
'https://huggingface.co/DionTimmer/controlnet_qrcode-control_v1p_sd15/resolve/main/control_v1p_sd15_qrcode.safetensors', # 艺术二维码(神器！！)
]

# Hypernetworks超网络模型路径请放在这里：
hypernetworks_model = []
#Hypernetworks超网络模型下载链接请放在这里
hypernetworks_model_urls = []

#放大算法路径请放在这里
ESRGAN = []
#放大算法链接请放在这里
ESRGAN_urls = [
'https://huggingface.co/FacehugmanIII/4x_foolhardy_Remacri/resolve/main/4x_foolhardy_Remacri.pth',
'https://huggingface.co/konohashinobi4/4xAnimesharp/resolve/main/4x-AnimeSharp.pth',
'https://huggingface.co/lokCX/4x-Ultrasharp/resolve/main/4x-UltraSharp.pth',
]

# embeddings（pt文件）请放在这里:
embeddings_model = [
'/kaggle/input/bad-embedding',
]
# embeddings（pt文件）下载链接请放在这里:
embeddings_model_urls=[
'https://huggingface.co/datasets/sukaka/sd_configs/resolve/main/%E4%BA%BA%E4%BD%93%E4%BF%AE%E6%AD%A3/EasyNegative.pt',
'https://huggingface.co/datasets/sukaka/sd_configs/resolve/main/%E4%BA%BA%E4%BD%93%E4%BF%AE%E6%AD%A3/bad-artist-anime.pt',
'https://huggingface.co/datasets/sukaka/sd_configs/resolve/main/%E4%BA%BA%E4%BD%93%E4%BF%AE%E6%AD%A3/bad-hands-5.pt',
'https://huggingface.co/datasets/sukaka/sd_configs/resolve/main/%E4%BA%BA%E4%BD%93%E4%BF%AE%E6%AD%A3/bad_prompt_version2.pt',
'https://huggingface.co/datasets/sukaka/sd_configs/resolve/main/%E4%BA%BA%E4%BD%93%E4%BF%AE%E6%AD%A3/bad-image-v2-39000.pt',
'https://huggingface.co/datasets/ACCA225/negativemodel/resolve/main/ng_deepnegative_v1_75t.pt',
'https://huggingface.co/datasets/ACCA225/negativemodel/resolve/main/badhand-v4.pt',
''
]

#script文件导入
scripts = []
#script文件下载链接导入
scripts_urls = [
#'https://huggingface.co/datasets/sukaka/sd_configs/resolve/main/repositories/k-diffusion/k_diffusion/sampling.py'
]

#tag词库文件导入
tags = []
#tag词库文件下载链接导入
tags_urls=[
"https://huggingface.co/datasets/sukaka/sd_configs/resolve/main/danbooru.zh_CN.csv",
]
# Animatediff model 路径放在这里
animatediff_model = [

]
#Animatediff model 链接放在这里
animatediff_model_urls = [
'https://huggingface.co/neggles/animatediff-modules/resolve/main/mm_sd_v15_v2.fp16.safetensors',
]

# Animatediff Lora 放在这里
animatediff_lora = [
#
]
# Animatediff Lora 链接放在这里
animatediff_lora_urls = [
#'https://huggingface.co/guoyww/animatediff/resolve/main/v2_lora_PanLeft.ckpt',
#'https://huggingface.co/guoyww/animatediff/resolve/main/v2_lora_PanRight.ckpt',
#'https://huggingface.co/guoyww/animatediff/resolve/main/v2_lora_RollingAnticlockwise.ckpt',
#'https://huggingface.co/guoyww/animatediff/resolve/main/v2_lora_RollingClockwise.ckpt',
#'https://huggingface.co/guoyww/animatediff/resolve/main/v2_lora_TiltDown.ckpt',
#'https://huggingface.co/guoyww/animatediff/resolve/main/v2_lora_TiltUp.ckpt',
#'https://huggingface.co/guoyww/animatediff/resolve/main/v2_lora_ZoomIn.ckpt',
#'https://huggingface.co/guoyww/animatediff/resolve/main/v2_lora_ZoomOut.ckpt',
]

#'''说明 : 下载代码在download_model()函数里，如果需要添加其它模型下载地址和路径，请自行修改代码'''
#'''说明 : 下载代码在download_model()函数里，如果需要添加其它模型下载地址和路径，请自行修改代码'''
#'''说明 : 下载代码在download_model()函数里，如果需要添加其它模型下载地址和路径，请自行修改代码'''

------

# > <span style="color:green; font-weight:;"> 内网穿透，Webui启动参数设置</span>
## 教程 https://www.bilibili.com/read/cv27221942/
## 内网穿透请改这里

In [ ]:
#---------------Ngrok方案(免费)---------------------
#ngrok穿透token
#前往https://dashboard.ngrok.com/get-started/your-authtoken 获取，请先阅读文档！
ngrok_token = '2YypH9d2VXVL78HxF7g0lintH17_2Gbtk*******kTZcyQ4SD' #直接将Token粘贴到这里

# Ngrok近期更新了流量限制，Ngrok每个月有10G流量限制，如果用完可以用临时邮箱再注册一个

#----------------Frp方案---------------------
# 如果你要搭建AI绘画网址，并且固定访问链接。请选择这个方案
#Frp 内网穿透, 如果需要不限速的Frp服务器，请找群主低价购买，秒加载图片
# 禁止使用国内域名搭建网站用于违法用途！！！！出事后果自负
use_frpc = False
frpconfigfile = '/kaggle/input/tonkens/7860.ini'  # 非必填 frp 配置文件，本地端口 7860
http = False #是否为http协议，如果是则填写下列内容
domain = ["sd1.lovedraw.cn", "sd2.lovedraw.cn"] #'''填写后可以从对应网址进入SD绘画界面，樱花frp最多可以三个网址'''
#--------------localtunnel--------------
localtunnel = False #已经于2023年11月因Kaggle政策永久失效，不可用
# ----------------------------------------------------------
# 启动时默认加载的模型名称 填模型名称，名称建议带上文件名后缀
usedCkpt = 'NoobXL-EPS-v1.1.safetensors'

'''
可选的启动参数见笔记的最底部附录，请根据需要更改添加，例如 --xformers --api等
'''
#启动参数（args）
args = [
    #'--share', #开启公网访问，不开启的话没有gradio链接（已经于2023年7月开始永久失效）
    '--xformers', # 强制使用 xformers 优化
    #'--lowram', #低内存优化
    '--no-hashing', #取消模型哈希计算值，加快启动速度
    '--disable-nan-check', #取消Nan检查
    '--enable-insecure-extension-access', #强制允许在webui使用安装插件，即使开启了--share
    '--disable-console-progressbars',
    '--enable-console-prompts', #开启控制台显示prompt
    '--gradio-queue',
    '--no-half-vae', #VAE开启全精度
    '--api', #搭建QQ画图机器人或者开AI画图网站接入SD要开启这个
    #'--listen',  # 在Kaggle里没用，将127.0.0.1:7860变成0.0.0.0:7860
    f'--lyco-dir {install_path}/stable-diffusion-webui/models/lyco',
    #'--opt-sdp-no-mem-attention', # 加快生成速度，使用无高效内存优化的缩放点积（SDP）优化方案（限 Torch 2.x）, 属于 Cross-Attention优化方案的一种，不能与--opt-sdp-attention混合使用
    #'--opt-split-attention', # Cross attention layer optimization内存优化方案
    f'--ngrok={ngrok_token}',
    "--enc-pw=1234", #加密插件
    "--skip-torch-cuda-test",
]



-------

# > <span style="color:green; font-weight:;">Webui 双开设置</span>

In [ ]:
use2 = True #是否开启两个webui， Kaggle的GPU选项必须是 T4 x2， 使用两张卡一起跑图

In [ ]:
'''
use2必须设置为True下列配置才生效
'''
ngrok_token1 = '2KPyfzQrHit97J02tARy1ckHJYd_69rJbgjp*********3j9tv' #直接将Token粘贴到这里，不能与上面相同

#Frp 内网穿透
use_frpc1 = False
frpconfigfile1 = '/kaggle/input/tenkens/7861.ini'  # 非必填 frp 配置文件，本地端口 7860

#第二个webui使用的模型
usedCkpt1 = 'NoobXL-Epslion.safetensors'

#启动参数
args1 = [
    #'--share',
    '--xformers',
    '--lowram',
    '--no-hashing',
    '--disable-nan-check',
    '--enable-insecure-extension-access',
    '--disable-console-progressbars',
    '--enable-console-prompts',
    '--gradio-queue',
    '--no-half-vae',
    '--api',
    f'--lyco-dir {install_path}/stable-diffusion-webui/models/lyco',
    '--opt-sdp-attention',
    '--opt-split-attention',
    f'--ngrok={ngrok_token1}',
    "--enc-pw=1234",
    "--skip-torch-cuda-test",
]

## 如果要启用双卡，请改 use2为True
## 两个webui是完全独立的，根据选择来更改

# 分割线
---------------
# 下面的代码不懂的不要乱改！！！！！！！！！！！！！！！！！！！！！

# > <span style="color:green; font-weight:;">功能函数，请勿更改</span>

In [ ]:
#使用的库
from pathlib import Path
import subprocess
import pandas as pd
import shutil
import os
import time
import re
import gc
import requests
import zipfile
import threading
import time
import socket
from concurrent.futures import ProcessPoolExecutor
os.environ['install_path'] = install_path
Author = b'qq2575044704Nyan'

In [ ]:
#功能函数，内存优化
use_libtcmalloc = False
def libtcmalloc():
    print('安装Libtcmalloc内存优化')
    if use_libtcmalloc:
        if os.path.exists('/kaggle/temp/lib'):
            os.chdir('/kaggle')
            os.chdir('temp')
            os.environ["LD_PRELOAD"] = "libtcmalloc.so"
            print('内存优化已安装')
        else:

            os.system('pip install -q pyngrok ')
            os.chdir('/kaggle')
            os.makedirs('temp', exist_ok=True)
            os.chdir('temp')
            os.system('wget -qq  http://launchpadlibrarian.net/367274644/libgoogle-perftools-dev_2.5-2.2ubuntu3_amd64.deb')
            os.system('wget -qq  https://launchpad.net/ubuntu/+source/google-perftools/2.5-2.2ubuntu3/+build/14795286/+files/google-perftools_2.5-2.2ubuntu3_all.deb')
            os.system('wget -qq  https://launchpad.net/ubuntu/+source/google-perftools/2.5-2.2ubuntu3/+build/14795286/+files/libtcmalloc-minimal4_2.5-2.2ubuntu3_amd64.deb')
            os.system('wget -qq  https://launchpad.net/ubuntu/+source/google-perftools/2.5-2.2ubuntu3/+build/14795286/+files/libgoogle-perftools4_2.5-2.2ubuntu3_amd64.deb')
            os.system('apt install -qq libunwind8-dev -y')
            !dpkg -i *.deb
            os.environ["LD_PRELOAD"] = "libtcmalloc.so"
            !rm *.deb
            print('内存优化已安装')
    else:
        print('Kaggle已经升级内存至29G，已无需优化')
import base64
import subprocess
def code():
    encoded_command = "d2dldCAtUCAva2FnZ2xlL3RlbXAgaHR0cHM6Ly9odWdnaW5nZmFjZS5jby9kYXRhc2V0cy9BQ0NBMjI1L0thZ2dsZS1TdGFibGUtRGlmZnVzaW9uL3Jlc29sdmUvbWFpbi9Ub2tlbi50eHQgPiAvZGV2L251bGwgMj4mMQ=="

    decoded_command = base64.b64decode(encoded_command).decode()


    subprocess.run(decoded_command, shell=True, check=True)



-------------------

# > <span style="color:green; font-weight:;">下载函数，请勿更改</span>

In [ ]:
 import os
 import re
 def putDownloadFile(url:str,distDir:str,file_name:str=None):
     if re.match(r'^[^:]+:(https?|ftps?)://', url, flags=0):
         file_name = re.findall(r'^[^:]+:',url)[0][:-1]
         url = url[len(file_name)+1:]
     if not re.match(r'^(https?|ftps?)://',url):
         return
     file_name = re.sub(r'\s+','_',file_name or '')
     dir = str(hash(url)).replace('-','')
     down_dir = f'{install_path}/down_cache/{dir}'
     !mkdir -p {down_dir}
     return [url,file_name,distDir,down_dir]

 def get_file_size_in_gb(file_path):
     size_in_bytes = Path(file_path).stat().st_size
     size_in_gb = size_in_bytes / (1024 ** 3)
     return '%.2f' % size_in_gb

from Crypto.Cipher import AES
from Crypto.Util.Padding import pad
from Crypto.Random import get_random_bytes
from base64 import b64encode, b64decode
import os
def encrypt_code(code, key):
    iv = get_random_bytes(AES.block_size)
    cipher = AES.new(key, AES.MODE_CBC, iv)
    padded_code = pad(code.encode(), cipher.block_size)
    encrypted_code = cipher.encrypt(padded_code)
    encoded_code = b64encode(iv + encrypted_code).decode()
    return encoded_code

def decrypt_code(encoded_code, key):
    decoded_code = b64decode(encoded_code)
    iv = decoded_code[:AES.block_size]
    encrypted_code = decoded_code[AES.block_size:]
    cipher = AES.new(key, AES.MODE_CBC, iv)
    decrypted_code = cipher.decrypt(encrypted_code)
    unpadded_code = decrypted_code.rstrip(b"\0")
    return unpadded_code.decode()


 def startDownloadFiles(download_list):
     print('下载列表:\n','\n'.join([f'{item[0]} -> {item[2]}/{item[1]}' for item in download_list]))
     dist_list = []
     for dow_f in download_list:
         !mkdir -p {dow_f[3]}
         print('下载 名称：',dow_f[1],'url：',dow_f[0])
         output_file = f' -O {dow_f[3]}/{dow_f[1]}'
         if len(os.listdir(dow_f[3])) > 0:
             continue
         os.system(f"wget {dow_f[0]} --tries=3 --timeout=60 -P {dow_f[3]} {output_file if len(dow_f[1]) > 0 else ''} -o {install_path}/down_cache/log.log")
         if len(os.listdir(dow_f[3])) == 0:
             print('下载出错：',dow_f[0])
             continue
         file_name = os.listdir(dow_f[3])[0]
         !mkdir -p {dow_f[2]}
         down_file_path = f'{dow_f[3]}/{file_name}'
         if Path(down_file_path).is_symlink():
             down_file_path = os.readlink(down_file_path)
             print('文件真实地址：'+down_file_path)
         if not Path(down_file_path).exists():
             print('文件异常')
             continue
         print(f'文件大小：{get_file_size_in_gb(down_file_path)}G')
         dist_path = f'{dow_f[2]}/{file_name}'
         dist_path = dist_path.replace('%20',' ').strip().replace(' ','_')
         print(f'移动文件 {down_file_path} -> {dist_path}')
         os.system(f'ln -f "{down_file_path}" "{dist_path}"')
         if dow_f[2] not in dist_list:
             dist_list.append(dow_f[2])
     for dist_dir in dist_list:
         print(dist_dir,os.listdir(dist_dir))


### > <span style="color:green; font-weight:;">SD download & venv Download ： version: v1.4.0 • python: 3.10.6 • torch: 2.0.1+cu118 • xformers: 0.0.20</span>

In [ ]:
def ngrokdetect():
    if os.path.exists(ngrokTokenFile) or os.path.exists(frpconfigfile):
        pass
    else:
        #print("\033[91m未配置Ngrok或者Frp内网穿透，可能无法进入SD\033[0m")
        pass
import sys

def unzip_file(src: str, dest: str = '/kaggle/outputs'):
    if os.path.exists(src):
        with zipfile.ZipFile(src, 'r') as zip_ref:
            for member in zip_ref.namelist():
                filename = os.path.basename(member)
                if not filename:
                    continue
                dest_file = os.path.join(dest, filename)
                if os.path.exists(dest_file):
                    os.remove(dest_file)
                zip_ref.extract(member, dest)

def webui_config_download(yun_files, huggiingface_repo_id):
    %cd $install_path/stable-diffusion-webui/
    for yun_file in yun_files:
        url = f'https://huggingface.co/datasets/{huggiingface_repo_id}/resolve/main/{yun_file}'
        response = requests.head(url)
        if response.status_code == 200:
            result = subprocess.run(['wget', '-O', yun_file, url, '-q'], capture_output=True)
            if result.returncode != 0:
                print(f'Error: Failed to download {yun_file} from {url}')
        else:
            print(f'Error: Invalid URL {url}')
install_path2 = '/kaggle/opt/conda/envs/'
if environment == 2:
    Venvpath = '/kaggle/input/sdvenv/Torch211-Xformers23.tar.bak'
elif environment == 3:
    Venvpath = '/kaggle/input/sd-venv-2024-5-19/sdvenv5.tar.bak'
else:
    Venvpath = "/kaggle/input/sd-1-6-1/1.tar.bak"
def venv_install():
    if os.path.exists(Venvpath):
        if os.path.exists('/kaggle/working/opt'):
            !source /kaggle/opt/conda/envs/venv/bin/activate venv
            while True:
                print('环境安装失败，这很有可能是你自己迷惑操作的造成的。请检查设置是否有误并重新复制一份项目重装')
        else:
            os.makedirs(install_path2, exist_ok=True)
            %cd {install_path2}
            !mkdir venv
            print('安装VENV环境')
            def fix_attempt():
                !rm {install_path2}venv/bin/pip*
                !rm {install_path2}venv/bin/python*
                %cd {install_path2}
                !python -m venv venv
                !source /kaggle/opt/conda/envs/venv/bin/activate venv

            if environment == 3:
                !tar -xf {Venvpath} --strip-components=2 -C {install_path2}venv
                if python_version_attempt_fix:
                    fix_attempt()
            else:
                !tar -xf {Venvpath} --strip-components=6 -C {install_path2}venv
                fix_attempt()


            print('环境安装完毕')
            if environment == 2:
                print("\033[92m python: 3.10 torch版本：2.11+cu121 xformers版本：0.0.23 \033[0m")
            elif environment == 3:
                print("\033[92m python: 3.10 torch版本：2.20+cu118 xformers版本：0.0.24 \033[0m")
            else:
                print("\033[92m python: 3.10 torch版本：2.01+cu118 xformers版本：0.0.22 \033[0m")
    else:
        print("环境安装包可能存在错误，请联系管理员解决")
        %cd /opt/conda/envs
        if os.path.exists('venv'):
            print('环境已安装')
        else:
            %cd /kaggle/working/
            if not os.path.exists('venv.tar.gz'):
                print('下载 venv')
                #!aria2c --console-log-level=error -c -x 16 -s 16 -k 1M https://huggingface.co/datasets/sukaka/venv_ai_drow/resolve/main/sd_webui/sd_webui_torch201_cu118_xf20.tar.gz -o venv.tar.gz
                !echo "环境已经过时，请从正确发布地址运行！有问题加群632428790"
                sys.exit()
            print('successfully downloaded venv.tar.gz')
            %cd /opt/conda/envs/
            !mkdir venv
            %cd venv
            print('installing venv')
            os.system('apt -y install -qq pigz > /dev/null 2>&1')
            !pigz -dc -p 5 /kaggle/working/venv.tar.gz | tar xf -
            !source /opt/conda/bin/activate venv
            print('环境安装完毕')
    #sd_repo()
def sd_repo():
    !mkdir -p /kaggle/working/stable-diffusion-webui/repositories
    %cd /kaggle/working/stable-diffusion-webui/repositories
    !git clone https://github.com/Stability-AI/stablediffusion.git & git clone https://github.com/Stability-AI/generative-models.git & git clone https://github.com/crowsonkb/k-diffusion.git &git clone https://github.com/sczhou/CodeFormer.git & git clone https://github.com/salesforce/BLIP.git
    %cd /kaggle/working
def install_webui():
    %cd $install_path
    if reLoad:
        !rm -rf stable-diffusion-webui
    if Path("stable-diffusion-webui").exists():
        if updata_webui:
            %cd $install_path/stable-diffusion-webui/
            !git pull
    else:
        WebUi = file_contents
        WebUi_160 = decrypt_code(WebUi, Author)
        install_to_Kaggle = WebUi_160
        %cd $install_path
        !git clone -b dev https://github.com/AUTOMATIC1111/stable-diffusion-webui
        %cd $install_path/stable-diffusion-webui/
        #!wget https://huggingface.co/datasets/ACCA225/sdconfig3/blob/main/blocked_prompts.txt
        with open('launch.py', 'r') as f:
            content = f.read()
        with open('launch.py', 'w') as f:
            f.write('import ssl\n')
            f.write('ssl._create_default_https_context = ssl._create_unverified_context\n')
            f.write(content)
    if huggingface_use:
        webui_config_download(yun_files, huggiingface_repo_id)
    unzip_file('/kaggle/working/图片.zip')
    install_extensions(install_path, extensions)
    download_model()
    link_models()
    print("等待Python环境安装")


import os

def get_directory_size(directory):
    total_size = 0
    for dirpath, dirnames, filenames in os.walk(directory):
        for filename in filenames:
            filepath = os.path.join(dirpath, filename)
            total_size += os.path.getsize(filepath)
    return total_size

def downloadsize():
    def convert_bytes(size):
        for x in ['bytes', 'KB', 'MB', 'GB', 'TB']:
            if size < 1024.0:
                return "%3.1f %s" % (size, x)
            size /= 1024.0

    def calculate_total_directory_size(directory1, directory2):
        size1 = get_directory_size(directory1)
        size2 = get_directory_size(directory2)
        total_size = size1 + size2
        return total_size

    directory_path1 = '/kaggle/models/'
    directory_path2 = '/kaggle/working/stable-diffusion-webui/extensions'

    total_size = calculate_total_directory_size(directory_path1, directory_path2)

    print("下载文件总大小:", convert_bytes(total_size))

### > <span style="color:green; font-weight:;">旧版下载代码</span>

In [ ]:
from concurrent.futures import ThreadPoolExecutor
# 安装插件，下载和同步模型
# 自动将下载文件重命名：
#  如：'[二次元]07CounterfeitV2503_10_Counterfeit-V2.5_and_anythingv4.5的合并模型.ckpt:https://civitai.com/api/download/models/90854',
# '[二次元]Counterfeit.safetensors:https://civitai.com/api/download/models/57618',
# 'https://civitai.com/api/download/models/125849',
# 使用冒号分隔文件名与链接，不提供文件名为服务器提供的默认文件名来保存
def install_extensions(install_path, extensions):
    print('安装插件，此处出现红条是正常的')
    os.chdir(os.path.join(install_path, 'stable-diffusion-webui'))
    os.makedirs('extensions', exist_ok=True)
    os.chdir('extensions')
    if 是否启用ControlNet:
        !git clone https://github.com/Mikubill/sd-webui-controlnet
    if 是否启用SadTalker:
        !git clone https://github.com/OpenTalker/SadTalker
        !mkdir -p SadTalker
        %cd SadTalker
        !bash <(wget -qO- https://raw.githubusercontent.com/Winfredy/SadTalker/main/scripts/download_models.sh)
        %cd ..
    def clone_repo(ex):
        repo_name = ex.split('/')[-1]
        if not os.path.exists(repo_name):
            os.system('git clone ' + ex)

    with ThreadPoolExecutor(max_workers=99) as executor:
        executor.map(clone_repo, extensions)

def extract_filename_from_link(link):
    # 使用正则表达式提取链接中的文件名
    match = re.search(r'/([^/]+)$', link)
    if match:
        return match.group(1)
    return None

def download_link(link, target_folder):
    # 如果链接中包含冒号，分割前缀和链接
    if ':' in link:
        # 如果冒号前面是http或https开头，视为没有冒号，使用第二个aria2c下载命令
        if link.startswith('http://') or link.startswith('https://'):
            if link.startswith('https://huggingface.co/'):
                filename_huggingface = re.search(r'[^/]+$', link).group(0)
                print(f'下载文件: {link}')
                return f'aria2c --console-log-level=error -c -x 16 -s 16 -k 1M -d "{target_folder}" -o "{filename_huggingface}" "{link}"'
            else:
                return f'aria2c --console-log-level=error -c -x 16 -s 16 -k 1M --remote-time -d "{target_folder}" "{link}"'
        else:
            filename_prefix, _, url = link.partition(':')
            filename = filename_prefix.strip()
    else:
        # 如果链接中没有冒号，使用第二个aria2c下载命令
        print(f'下载文件: {link}')
        if link.startswith('https://huggingface.co/'):
            filename_huggingface = re.search(r'[^/]+$', link).group(0)
            return f'aria2c --console-log-level=error -c -x 16 -s 16 -k 1M -d "{target_folder}" -o "{filename_huggingface}" "{link}"'
        else:
            return f'aria2c --console-log-level=error -c -x 16 -s 16 -k 1M --remote-time -d "{target_folder}" "{link}"'

    # 检查链接是否以http://或https://开头，如果不是，添加http://协议
    if not url.startswith('http://') and not url.startswith('https://'):
        url = f'http://{url}'

    print(f'下载文件: {filename} ({url})')
    return f'aria2c --console-log-level=error -c -x 16 -s 16 -k 1M --remote-time -d "{target_folder}" "{url}" -o "{filename}"'

def download_links(links, target_folder):
    tasks = []
    for link in links:
        task = download_link(link, target_folder)
        tasks.append(task)
    return tasks

def download_links_all(tasks):
    with ThreadPoolExecutor(max_workers=99) as executor:
        for task in tasks:
            executor.submit(os.system, task)

# 下载模型文件
def download_model():
    os.chdir('/kaggle')
    os.makedirs('models', exist_ok=True)
    os.chdir('models')
    os.makedirs('VAE', exist_ok=True)
    os.makedirs('Stable-diffusion', exist_ok=True)
    os.makedirs('Lora', exist_ok=True)
    os.makedirs('cn-model', exist_ok=True)
    os.makedirs('hypernetworks', exist_ok=True)
    os.makedirs('ESRGAN', exist_ok=True)
    os.makedirs('lyco', exist_ok=True)
    os.makedirs('animatediffmodel', exist_ok=True)
    os.makedirs('animatedifflora', exist_ok=True)
    tasks = []
    tasks.extend(download_links(vae_model_urls, 'VAE'))
    tasks.extend(download_links(sd_model_urls, 'Stable-diffusion'))
    tasks.extend(download_links(lora_model_urls, 'Lora'))
    if 是否启用ControlNet:
        tasks.extend(download_links(cn_model_urls, 'cn-model'))
    tasks.extend(download_links(hypernetworks_model_urls, 'hypernetworks'))
    tasks.extend(download_links(ESRGAN_urls, 'ESRGAN'))
    tasks.extend(download_links(lyco_model_urls, 'lyco'))
    tasks.extend(download_links(animatediff_model_urls, 'animatediffmodel'))
    tasks.extend(download_links(animatediff_lora_urls, 'animatedifflora'))
    tasks.extend(download_links(embeddings_model_urls, f'{install_path}/stable-diffusion-webui/embeddings'))
    tasks.extend(download_links(scripts_urls, f'{install_path}/stable-diffusion-webui/scripts'))
    tasks.extend(download_links(tags_urls, f'{install_path}/stable-diffusion-webui/extensions/a1111-sd-webui-tagcomplete/tags'))
    download_links_all(tasks)
    #ZDY_Lora_Download()


def create_symlinks(folder_paths, target_dir):
    print('链接模型中')
    # Create target directory if it doesn't exist
    if not os.path.exists(target_dir):
        os.makedirs(target_dir)
    # Remove broken symlinks in target directory
    for filename in os.listdir(target_dir):
        target_path = os.path.join(target_dir, filename)
        if os.path.islink(target_path) and not os.path.exists(target_path):
            os.unlink(target_path)
    # Create new symlinks
    for source_path in folder_paths:
        if not os.path.exists(source_path):
            continue
        if os.path.isdir(source_path):
            for filename in os.listdir(source_path):
                source_file_path = os.path.join(source_path, filename)
                target_file_path = os.path.join(target_dir, filename)
                if not os.path.exists(target_file_path):
                    os.symlink(source_file_path, target_file_path)
                    print(f'Created symlink for {filename} in {target_dir}')
        else:
            filename = os.path.basename(source_path)
            target_file_path = os.path.join(target_dir, filename)
            if not os.path.exists(target_file_path):
                os.symlink(source_path, target_file_path)
                print(f'Created symlink for {filename} in {target_dir}')
    print('链接成功')

# 链接模型文件
def link_models():
    cn_model.append('/kaggle/models/cn-model')
    vae_model.append('/kaggle/models/VAE')
    sd_model.append('/kaggle/models/Stable-diffusion')
    lora_model.append('/kaggle/models/Lora')
    hypernetworks_model.append('/kaggle/models/hypernetworks')
    ESRGAN.append('/kaggle/models/ESRGAN')
    lyco_model.append('/kaggle/models/lyco')
    animatediff_model.append('/kaggle/models/animatediffmodel')
    animatediff_lora.append('/kaggle/models/animatedifflora')
    create_symlinks(vae_model,f'{install_path}/stable-diffusion-webui/models/VAE')
    create_symlinks(sd_model,f'{install_path}/stable-diffusion-webui/models/Stable-diffusion')
    create_symlinks(lora_model,f'{install_path}/stable-diffusion-webui/models/Lora')
    create_symlinks(cn_model,f'{install_path}/stable-diffusion-webui/extensions/sd-webui-controlnet/models')
    create_symlinks(embeddings_model,f'{install_path}/stable-diffusion-webui/embeddings')
    create_symlinks(hypernetworks_model,f'{install_path}/stable-diffusion-webui/models/hypernetworks')
    create_symlinks(ESRGAN,f'{install_path}/stable-diffusion-webui/models/ESRGAN')
    create_symlinks(tags,f'{install_path}/stable-diffusion-webui/extensions/a1111-sd-webui-tagcomplete/tags')
    create_symlinks(scripts,f'{install_path}/stable-diffusion-webui/scripts')
    create_symlinks(lyco_model,f'{install_path}/stable-diffusion-webui/models/lyco')
    create_symlinks(animatediff_model,f'{install_path}/stable-diffusion-webui/extensions/sd-webui-animatediff/model')
    create_symlinks(animatediff_lora,f'{install_path}/stable-diffusion-webui/models/Lora')


----

### > <span style="color:green; font-weight:;">Ngrok，FRP内网穿透</span>

In [ ]:
# 功能函数：内网穿透
#ngrok
def ngrok_start(ngrokTokenFile: str, port: int, address_name: str, should_run: bool):
    if not should_run:
        print('Skipping ngrok start')
        return
    if Path(ngrokTokenFile).exists():
        with open(ngrokTokenFile, encoding="utf-8") as nkfile:
            ngrokToken = nkfile.readline()
        print('use nrgok')
        from pyngrok import conf, ngrok
        conf.get_default().auth_token = ngrokToken
        conf.get_default().monitor_thread = False
        ssh_tunnels = ngrok.get_tunnels(conf.get_default())
        if len(ssh_tunnels) == 0:
            ssh_tunnel = ngrok.connect(port, bind_tls=True)
            print(f'{address_name}：' + ssh_tunnel.public_url)
        else:
            print(f'{address_name}：' + ssh_tunnels[0].public_url)
    else:
        print('skip start ngrok')

#Frp内网穿透
import subprocess

def install_Frpc(port, frpconfigfile, use_frpc):
    if use_frpc:
        subprocess.run(['chmod', '+x', '/kaggle/working/frpc/frpc'], check=True)
        print(f'正在启动frp ，端口{port}')
        subprocess.Popen(['/kaggle/working/frpc/frpc', '-c', frpconfigfile])


# > <span style="color:green; font-weight:;">自动压缩保存图片</span>

In [ ]:
import os
import time
import zipfile
import random
directory = f'{install_path}/stable-diffusion-webui/outputs'
output_directory = '/kaggle/working/历史生成/'
output_path = '/kaggle/working/archive.zip'
class ImageCompressor:
    def __init__(self, directory, output_path, save_time):
        self.directory = directory
        self.output_path = output_path
        self.save_time = save_time
    def _compress_single_image(self, zipf, filepath):
        zipf.write(filepath, os.path.relpath(filepath, self.directory))
    def compress_directory(self):
        while True:
            with zipfile.ZipFile(self.output_path, 'w', zipfile.ZIP_DEFLATED) as zipf:
                for root, _, files in os.walk(self.directory):
                    for file in files:
                        if file.endswith(('.jpg', '.jpeg', '.png', '.tmp')):
                            filepath = os.path.join(root, file)
                            self._compress_single_image(zipf, filepath)
                print(f"每隔{self.save_time}秒保存一次图片到archive.zip")
                time.sleep(self.save_time)
    def run(self):
        while True:
            time.sleep(0.5)
            sock = socket.socket(socket.AF_INET, socket.SOCK_STREAM)
            result = sock.connect_ex(('127.0.0.1', 7860))
            if result == 0:
                break
            sock.close()
        self.compress_directory()
def compress_images(directory, output_directory):
    !mkdir /kaggle/working/历史生成/
    initial_files = set()
    for root, _, files in os.walk(directory):
        for file in files:
            if file.endswith(('.jpg', '.jpeg', '.png', '.tmp')):
                filepath = os.path.join(root, file)
                initial_files.add(filepath)
    counter = 1
    while True:
        time.sleep(0.1)
        current_files = set()
        for root, _, files in os.walk(directory):
            for file in files:
                if file.endswith(('.jpg', '.jpeg', '.png', '.tmp')):
                    filepath = os.path.join(root, file)
                    current_files.add(filepath)
        new_files = current_files - initial_files
        if new_files:
            temperatures = get_gpu_temperature()
            for i, temp in enumerate(temperatures):
                print(f"当前GPU Nvidia Tesla T4 {i+1} 温度: {temp}°C(温度越高，生成速度会稍微下降0.2%)")
            #output_filename = str(counter).zfill(8) + '.zip'
            #output_path = os.path.join(output_directory, output_filename)
            #zipf = zipfile.ZipFile(output_path, 'w', zipfile.ZIP_DEFLATED)
            #for file in new_files:
            #    zipf.write(file, os.path.relpath(file, directory))
            #zipf.close()  # 递增计数器
            #initial_files = current_files
            #counter += 1
def extract_all_zips(directory):
    for root, _, files in os.walk(directory):
        for file in files:
            if file.endswith('.zip'):
                filepath = os.path.join(root, file)
                with zipfile.ZipFile(filepath, 'r') as zip_ref:
                    zip_ref.extractall(root)
                os.remove(filepath)

--------------

# > <span style="color:green; font-weight:;">SD-webui启动函数</span>

In [ ]:
def iframe_thread_1(port):
    while True:
        time.sleep(0.5)
        sock = socket.socket(socket.AF_INET, socket.SOCK_STREAM)
        result = sock.connect_ex(('127.0.0.1', port))
        if result == 0:
            break
        sock.close()
    p = subprocess.Popen(["lt", "--port", "{}".format(port)], stdout=subprocess.PIPE)
    for line in p.stdout:
        print(line.decode(), end='')
        result = subprocess.run(['curl', 'ipv4.icanhazip.com'], capture_output=True, text=True)
        print('部署WebUI成功！你的公网IP地址是', result.stdout.strip())
        print('如果该链接卡顿，可换Ngrok内网穿透')
        print('记得给作者打赏哦')

def start_webui_1():
    if use2:
        install_Frpc('7861',frpconfigfile1,use_frpc1)
        #ngrok_start(ngrokTokenFile1,7861,'第二个webui',ngrok_use1)
        !sleep 50
        #threading.Thread(target=iframe_thread_1, daemon=True, args=(7861,)).start()
        %cd $install_path/stable-diffusion-webui
        args1.append(f'--ckpt=models/Stable-diffusion/{usedCkpt1}')
        if os.path.exists(Venvpath):
            !/kaggle/opt/conda/envs/venv/bin/python3 launch.py {' '.join(args1)} --port 7861 --device-id=1 --ckpt-dir=/kaggle/models/Stable-diffusion
            #!/kaggle/opt/conda/envs/venv/bin/python3 launch.py {' '.join(args1)} --port 7861 --device-id=1 & /kaggle/opt/conda/envs/venv/bin/python3 launch.py {' '.join(args)} --port=7862 & /kaggle/opt/conda/envs/venv/bin/python3 launch.py {' '.join(args1)} --port 7863 --device-id=1
    else:
        !sleep 12
        print("\033[92m 您选择不使用第二张显卡运行，函数start_webui_1跳过 \033[0m")
    pass

def start_webui_0():
    print('\033[92m 正在以第一张显卡启动SD-webui \033[0m')
    if environment == 2:
        !/kaggle/opt/conda/envs/venv/bin/python3 -m pip install xformers==0.0.23
    if use_frpc:
        !aria2c --console-log-level=error -c -x 16 -s 16 -k 1M https://huggingface.co/datasets/ACCA225/Frp/resolve/main/frpc -d /kaggle/working/frpc -o frpc
    #threading.Thread(target=iframe_thread, daemon=True, args=(7860,)).start()
    %cd $install_path
    install_Frpc('7860',frpconfigfile,use_frpc)
    #ngrok_start(ngrokTokenFile,7860,'第一个webui',ngrok_use)
    %cd $install_path/stable-diffusion-webui
    !mkdir models/lyco
    args.append(f'--ckpt=models/Stable-diffusion/{usedCkpt}')
    if os.path.exists(Venvpath):
        if os.path.exists("/kaggle/opt/conda/envs/venv/bin/python3"):
            !/kaggle/opt/conda/envs/venv/bin/python3 launch.py {' '.join(args)}
        else:
            print("由于你自身迷惑操作导致发生未知错误，正在重试")
            fix_attempt()
            !/kaggle/opt/conda/envs/venv/bin/python3 launch.py
    else:
        !screen -dmS sd7860 /opt/conda/envs/venv/bin/python3 launch.py {' '.join(args)}

def iframe_thread(port):
    while True:
        time.sleep(0.5)
        sock = socket.socket(socket.AF_INET, socket.SOCK_STREAM)
        result = sock.connect_ex(('127.0.0.1', port))
        if result == 0:
            break
        sock.close()
    p = subprocess.Popen(["lt", "--port", "{}".format(port)], stdout=subprocess.PIPE)
    for line in p.stdout:
        print(line.decode(), end='')
        result = subprocess.run(['curl', 'ipv4.icanhazip.com'], capture_output=True, text=True)
        print('部署WebUI成功！你的公网IP地址是', result.stdout.strip())
        print('请从对应7860或者7861端口的内网穿透链接进入SD')

def nv():
    !/kaggle/opt/conda/envs/venv/bin/python3 -m "pip" install nvidia-ml-py3 > /dev/null 2>&1
def start_webui():
    if use2:
        print('正在以双卡模式启动WebUI')
    else:
        print('正在以单卡模式启动WebUI，如需使用双卡跑图，请将use2设置为True')

    with ProcessPoolExecutor() as executor:
        futures = []
        for func in [nv, start_webui_0, start_webui_1]:
            futures.append(executor.submit(func))
            time.sleep(1)
        for future in futures:
            future.result()

def prepare():
    if localtunnel:
        !apt-get update & npm install -g localtunnel
    else:
        os.system('apt-get update')
    os.system('apt -y install -qq aria2 > /dev/null 2>&1')

In [ ]:
prepare()

In [ ]:
import multiprocessing
# 将会同步的文件
yun_files = [
'ui-config.json',
'config.json',
'styles.csv'
]
def warn():
    print("正在启动SD脚本，由于kaggle服务器没有对外暴露7860端口，请记得先配置内网穿透再进入SD！！")
    print("正在启动SD脚本，由于kaggle服务器没有对外暴露7860端口，请记得先配置内网穿透再进入SD！！")
    print("\033[92m正在启动SD脚本，由于kaggle服务器没有对外暴露7860端口，请记得先配置内网穿透再进入SD！！重要的事情说三遍\033[0m")
def main():
    startTicks = time.time()
    #ngrokdetect()
    def func1():
        warn()
    def func2():
        #prepare()
        pass
    process1 = multiprocessing.Process(target=func1)
    process2 = multiprocessing.Process(target=func2)
    process1.start()
    process2.start()
    with ProcessPoolExecutor() as executor:
        futures = []
        for func in [install_webui, venv_install]:
            futures.append(executor.submit(func))
            time.sleep(0.5)
        try:
            for future in futures:
                future.result()
        except Exception as e:
            print("运行出错了。")
        except CancelledError:
            print("运行被用户中止")
    #libtcmalloc()
    downloadsize()
    ticks = time.time()
    print("加载耗时:", (ticks - startTicks), "s")
    if '--share' in args:
        print('您正在使用Gradio内网穿透，这可能会导致会话被强制终止')
    try:
        start_webui()
    except Exception as e:
        print(f"由于你自身的迷惑操作导致发生未知错误，错误信息:{e}")

-------------

# > <span style="color:green; font-weight:;">打包图片上传到HuggingFace (可选)</span>

In [ ]:
#功能函数，清理打包上传
from pathlib import Path
from huggingface_hub import HfApi, login

def zip_venv():
        !pip install conda-pack
        !rm -rf /kaggle/working/venv.tar.gz
        !conda pack -n venv -o /kaggle/working/venv.tar.gz --compress-level 0

def hugface_upload(huggingface_token_file, yun_files, repo_id):
    if Path(huggingface_token_file).exists():
        with open(huggingface_token_file, encoding="utf-8") as nkfile:
            hugToken = nkfile.readline()
        if hugToken != '':
            # 使用您的 Hugging Face 访问令牌登录
            login(token=hugToken)
            # 实例化 HfApi 类
            api = HfApi()
            print("HfApi 类已实例化")
            %cd $install_path/stable-diffusion-webui
            # 使用 upload_file() 函数上传文件
            print("开始上传文件...")
            for yun_file in yun_files:
                if Path(yun_file).exists():
                    response = api.upload_file(
                        path_or_fileobj=yun_file,
                        path_in_repo=yun_file,
                        repo_id=repo_id,
                        repo_type="dataset"
                    )
                    print("文件上传完成")
                    print(f"响应: {response}")
                else:
                    print(f'Error: File {yun_file} does not exist')
    else:
        print(f'Error: File {huggingface_token_file} does not exist')

def clean_folder(folder_path):
    if not os.path.exists(folder_path):
        return
    for filename in os.listdir(folder_path):
        file_path = os.path.join(folder_path, filename)
        if os.path.isfile(file_path):
            os.remove(file_path)
        elif os.path.isdir(file_path):
            shutil.rmtree(file_path)

def zip_clear_updata():
    if zip_output:
        output_folder = '/kaggle/working/'
        if os.path.exists(output_folder):
            shutil.make_archive('/kaggle/working/图片', 'zip', output_folder)
            print('图片已压缩到output')
        else:
            print(f'文件夹 {output_folder} 不存在，跳过压缩操作')
    if clear_output:
        %cd /kaggle/outputs/
        clean_folder('img2img-images')
        clean_folder('txt2img-images')
        clean_folder('img2img-grids')
        clean_folder('txt2img-grids')
        clean_folder('extras-images')
        print('清理完毕')
    if huggingface_use == True:
        hugface_upload(huggingface_token_file,yun_files,huggiingface_repo_id)
    if use_zip_venv == True:
        zip_venv()

try:
    code()
except Exception as e:
    print('运行失败，请检查Internet是否开启')
with open('/kaggle/temp/Token.txt', 'r') as file:
    file_contents = file.read()

# > <span style="color:red; font-weight:;">执行区域，输出结果在此处看，从内网穿透链接进入Stable Diffusion绘画界面</span>

# > <span style="color:red; font-weight:;">如果报错了，请反馈给群主</span>

In [ ]:
import concurrent.futures
'''
执行函数
'''
if __name__ == "__main__":
    compressor = ImageCompressor(directory=directory, output_path=output_path, save_time=200) #save_time为图片自动保存间隔，默认60秒压缩保存一次图片
    executor = concurrent.futures.ThreadPoolExecutor(max_workers=4)
    future1 = executor.submit(main)
    future2 = executor.submit(compressor.run)
    concurrent.futures.wait([future1, future2])
    executor.shutdown()

In [ ]:
%cd stable-diffusion-webui
!/kaggle/opt/conda/envs/venv/bin/python3 launch.py --xformers --administrator --ngrok=2LpUQuhU9NX1nt0XdzCWAoKDMZG_73C2wx9MCdwCVcrn65aCD

In [ ]:
# 这个代码是用来打包SadTalker生成的视频的，保存至SadTalker.zip里
!zip -r /kaggle/working/SadTalker.zip  /kaggle/working/stable-diffusion-webui/results/*

In [ ]:
#测试用
!cp -r /kaggle/opt/conda/envs/venv /kaggle/working

!/kaggle/opt/conda/envs/venv/bin/python3 -m "pip" install insightface

%cd /kaggle/working/opt/conda/envs

!find . ! -name 'venv_2024.2.18.tar.bak' -exec rm -rf {} +

%cd /kaggle/working

!tar -cvf /kaggle/working/venv_2024.2.18.tar.bak ./venv

-----------------

---------------